### Import Libraries and Data

In [98]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import contextily as ctx
import folium
import branca.colormap as cm
from folium.features import GeoJsonTooltip

In [99]:
# Rental Price Predictions Data 
one_bed_flat_pred = pd.read_csv('../data/curated/predictions/one_bed_flat_predictions.csv')
two_bed_flat_pred = pd.read_csv('../data/curated/predictions/two_bed_flat_predictions.csv')
three_bed_flat_pred = pd.read_csv('../data/curated/predictions/three_bed_flat_predictions.csv')
two_bed_house_pred = pd.read_csv('../data/curated/predictions/two_bed_house_predictions.csv')
three_bed_house_pred = pd.read_csv('../data/curated/predictions/three_bed_house_predictions.csv')
four_bed_house_pred = pd.read_csv('../data/curated/predictions/four_bed_house_predictions.csv')
all_properties_pred = pd.read_csv('../data/curated/predictions/all_properties_predictions.csv')

# Merged Data
one_bed_flat_merged = pd.read_csv('../data/curated/merged_feature_set/one_bed_flat_merged.csv')
two_bed_flat_merged = pd.read_csv('../data/curated/merged_feature_set/two_bed_flat_merged.csv')
three_bed_flat_merged = pd.read_csv('../data/curated/merged_feature_set/three_bed_flat_merged.csv')
two_bed_house_merged = pd.read_csv('../data/curated/merged_feature_set/two_bed_house_merged.csv')
three_bed_house_merged = pd.read_csv('../data/curated/merged_feature_set/three_bed_house_merged.csv')
four_bed_house_merged = pd.read_csv('../data/curated/merged_feature_set/four_bed_house_merged.csv')
all_properties_merged = pd.read_csv('../data/curated/merged_feature_set/all_properties_merged.csv')

# Load Victoria suburbs shapefile for filtering
vic_suburbs_gdf = gpd.read_file('../data/raw/Vic_Localities/gda2020_vicgrid/esrishape/whole_of_dataset/victoria/VMADMIN/LOCALITY_POLYGON.shp')
vic_suburbs_gdf = vic_suburbs_gdf.to_crs(epsg=4326)
vic_suburbs_gdf['suburb'] = vic_suburbs_gdf['GAZLOC'].str.lower()

### Calculate Growth Rate 

In [102]:
# Add the 2024 rental prices for the growth rate calculation

# List of columns to keep
columns_to_keep = ['suburb', 'year', 'dec_median', 'mar_median']

# Append rows only if suburbs match, keeping only specified columns
one_bed_flat_2024 = one_bed_flat_merged[(one_bed_flat_merged['year'] == 2024) & 
                                        (one_bed_flat_merged['suburb'].isin(one_bed_flat_pred['suburb']))][columns_to_keep]
two_bed_flat_2024 = two_bed_flat_merged[(two_bed_flat_merged['year'] == 2024) & 
                                        (two_bed_flat_merged['suburb'].isin(two_bed_flat_pred['suburb']))][columns_to_keep]
three_bed_flat_2024 = three_bed_flat_merged[(three_bed_flat_merged['year'] == 2024) & 
                                            (three_bed_flat_merged['suburb'].isin(three_bed_flat_pred['suburb']))][columns_to_keep]
two_bed_house_2024 = two_bed_house_merged[(two_bed_house_merged['year'] == 2024) & 
                                          (two_bed_house_merged['suburb'].isin(two_bed_house_pred['suburb']))][columns_to_keep]
three_bed_house_2024 = three_bed_house_merged[(three_bed_house_merged['year'] == 2024) & 
                                              (three_bed_house_merged['suburb'].isin(three_bed_house_pred['suburb']))][columns_to_keep]
four_bed_house_2024 = four_bed_house_merged[(four_bed_house_merged['year'] == 2024) & 
                                            (four_bed_house_merged['suburb'].isin(four_bed_house_pred['suburb']))][columns_to_keep]
all_properties_2024 = all_properties_merged[(all_properties_merged['year'] == 2024) & 
                                            (all_properties_merged['suburb'].isin(all_properties_pred['suburb']))][columns_to_keep]

# Append matching rows to their respective prediction dataframes (gr = growth rate)
one_bed_flat_gr = pd.concat([one_bed_flat_pred, one_bed_flat_2024], ignore_index=True)[columns_to_keep]
two_bed_flat_gr = pd.concat([two_bed_flat_pred, two_bed_flat_2024], ignore_index=True)[columns_to_keep]
three_bed_flat_gr = pd.concat([three_bed_flat_pred, three_bed_flat_2024], ignore_index=True)[columns_to_keep]
two_bed_house_gr = pd.concat([two_bed_house_pred, two_bed_house_2024], ignore_index=True)[columns_to_keep]
three_bed_house_gr = pd.concat([three_bed_house_pred, three_bed_house_2024], ignore_index=True)[columns_to_keep]
four_bed_house_gr = pd.concat([four_bed_house_pred, four_bed_house_2024], ignore_index=True)[columns_to_keep]
all_properties_gr = pd.concat([all_properties_pred, all_properties_2024], ignore_index=True)[columns_to_keep]
all_properties_pred[all_properties_pred['suburb'] == 'melbourne']

suburb  year  dec_median  jun_median  mar_median  sep_median
345  melbourne  2025      606.65      597.55      592.30     611.975
346  melbourne  2026      587.18      578.10      572.63     599.245
347  melbourne  2027      585.73      576.05      570.50     600.995

In [101]:
# Function to calculate growth rate between 2024 and 2027
def calculate_growth_rate(df, vic_suburbs_gdf):
    # Filter for 2024 and 2027 data
    df_2024 = df[df['year'] == 2024][['suburb', 'mar_median']]
    df_2027 = df[df['year'] == 2027][['suburb', 'dec_median']]
    
    # Merge the 2024 and 2027 data on 'suburb' to compare growth
    growth_df = pd.merge(df_2024, df_2027, on='suburb', how='inner')
    
    # Calculate growth rate
    growth_df['growth_rate'] = (growth_df['dec_median'] - growth_df['mar_median']) / growth_df['mar_median'] * 100

    # Add geometry column for plotting 
    growth_df = pd.merge(growth_df, vic_suburbs_gdf[['suburb', 'geometry']], on='suburb', how='inner')

    return growth_df[['suburb', 'growth_rate', 'geometry']]

# Applying to each dataframe
one_bed_flat_gr = calculate_growth_rate(one_bed_flat_gr, vic_suburbs_gdf)
two_bed_flat_gr = calculate_growth_rate(two_bed_flat_gr, vic_suburbs_gdf)
three_bed_flat_gr = calculate_growth_rate(three_bed_flat_gr, vic_suburbs_gdf)
two_bed_house_gr = calculate_growth_rate(two_bed_house_gr, vic_suburbs_gdf)
three_bed_house_gr = calculate_growth_rate(three_bed_house_gr, vic_suburbs_gdf)
four_bed_house_gr = calculate_growth_rate(four_bed_house_gr, vic_suburbs_gdf)
all_properties_gr = calculate_growth_rate(all_properties_gr, vic_suburbs_gdf)
all_properties_gr[all_properties_gr['suburb'] == 'melbourne']

suburb  growth_rate                                           geometry
115  melbourne    -8.479687  POLYGON ((144.97798 -37.83865, 144.97805 -37.8...

#### Growth Rate Visualisation

In [96]:
# Assuming your dataframe is already a GeoDataFrame
gdf = gpd.GeoDataFrame(one_bed_flat_gr, geometry='geometry')

# Reproject to WGS84 (lat/long format) for folium compatibility
gdf = gdf.to_crs(epsg=4326)

# Create a folium map centered around the coordinates of the data
m = folium.Map(location=[-37.8136, 144.9631], zoom_start=10)

# Create a colormap (green for positive, red for negative)
colormap = cm.LinearColormap(colors=['red', 'yellow', 'green'], vmin=gdf['growth_rate'].min(), vmax=gdf['growth_rate'].max())
colormap.caption = 'Growth Rate (%)'

# Add polygons to the map with the proper color
folium.GeoJson(
    gdf,
    style_function=lambda feature: {
        'fillColor': colormap(feature['properties']['growth_rate']),
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.7,
    },
    tooltip=GeoJsonTooltip(
        fields=['suburb', 'growth_rate'],
        aliases=['Suburb: ', 'Growth Rate: '],
        localize=True
    )
).add_to(m)

# Add the colormap to the map
colormap.add_to(m)

# Display the map
m.save('interactive_growth_rate_map.html')

m  # This will display the map in a Jupyter environment or you can open the saved HTML
